In [62]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from category_encoders import BaseNEncoder
from sklearn.model_selection import train_test_split
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import RandomizedSearchCV
from catboost import CatBoostClassifier
from sklearn.metrics import log_loss
from sklearn.metrics import accuracy_score
from sklearn import model_selection
import scipy.stats as stats
from sklearn.feature_selection import SelectFromModel

In [63]:
train = pd.read_csv('../../Feature_Engineering/data/other-cleaned_train.csv')
test = pd.read_csv('../../Feature_Engineering/data/other-cleaned_test.csv')

In [64]:
train.drop(columns = ['Unnamed: 0'], inplace = True)
test.drop(columns = ['Unnamed: 0'], inplace = True)

In [65]:
X_train = train.copy()
X_test = test.copy()

In [66]:
categ_columns = train.drop(columns = ["Opportunity_ID","ID", "Pricing, Delivery_Terms_Quote_Appr",\
                                    "Bureaucratic_Code_0_Approval","Bureaucratic_Code_0_Approved",\
                                    "Submitted_for_Approval","ASP","ASP_(converted)","TRF","Total_Amount",\
                                    "Total_Taxable_Amount","diferencia_en_dias","Last_Modified_DOY","Last_Modified_Year",\
                                    "Opportunity_Created_DOY","Opportunity_Created_Year","Quote_Expiry_DOY",\
                                     "Quote_Expiry_Year","Planned_Delivery_Start_DOY","Planned_Delivery_Start_Year",\
                                    "Planned_Delivery_End_DOY","Planned_Delivery_End_Year",\
                                    "Target"]).columns
for column in categ_columns:
    encoder = BaseNEncoder(base = 5)
    encoder.fit(train[column], train['Target'])
    feature_encoded = encoder.transform(train[column])
    X_train = X_train.join(feature_encoded.add_suffix('_base_n'))
    X_train.drop(columns=[column], inplace = True)

C:\Users\ferna\Anaconda3\lib\site-packages\category_encoders\utils.py:21: FutureWarning: is_categorical is deprecated and will be removed in a future version.  Use is_categorical_dtype instead
  elif pd.api.types.is_categorical(cols):
C:\Users\ferna\Anaconda3\lib\site-packages\category_encoders\utils.py:21: FutureWarning: is_categorical is deprecated and will be removed in a future version.  Use is_categorical_dtype instead
  elif pd.api.types.is_categorical(cols):
C:\Users\ferna\Anaconda3\lib\site-packages\category_encoders\utils.py:21: FutureWarning: is_categorical is deprecated and will be removed in a future version.  Use is_categorical_dtype instead
  elif pd.api.types.is_categorical(cols):
C:\Users\ferna\Anaconda3\lib\site-packages\category_encoders\utils.py:21: FutureWarning: is_categorical is deprecated and will be removed in a future version.  Use is_categorical_dtype instead
  elif pd.api.types.is_categorical(cols):
C:\Users\ferna\Anaconda3\lib\site-packages\category_encoders

In [67]:
categ_columns = test.drop(columns = ["Opportunity_ID","ID", "Pricing, Delivery_Terms_Quote_Appr",\
                                    "Bureaucratic_Code_0_Approval","Bureaucratic_Code_0_Approved",\
                                    "Submitted_for_Approval","ASP","ASP_(converted)","TRF","Total_Amount",\
                                    "Total_Taxable_Amount","diferencia_en_dias","Last_Modified_DOY","Last_Modified_Year",\
                                    "Opportunity_Created_DOY","Opportunity_Created_Year","Quote_Expiry_DOY",\
                                     "Quote_Expiry_Year","Planned_Delivery_Start_DOY","Planned_Delivery_Start_Year",\
                                    "Planned_Delivery_End_DOY","Planned_Delivery_End_Year"]).columns
for column in categ_columns:
    encoder = BaseNEncoder(base = 5)
    encoder.fit(train[column], train['Target'])
    feature_encoded = encoder.transform(test[column])
    X_test = X_test.join(feature_encoded.add_suffix('_base_n'))
    X_test.drop(columns=[column], inplace = True)

C:\Users\ferna\Anaconda3\lib\site-packages\category_encoders\utils.py:21: FutureWarning: is_categorical is deprecated and will be removed in a future version.  Use is_categorical_dtype instead
  elif pd.api.types.is_categorical(cols):
C:\Users\ferna\Anaconda3\lib\site-packages\category_encoders\utils.py:21: FutureWarning: is_categorical is deprecated and will be removed in a future version.  Use is_categorical_dtype instead
  elif pd.api.types.is_categorical(cols):
C:\Users\ferna\Anaconda3\lib\site-packages\category_encoders\utils.py:21: FutureWarning: is_categorical is deprecated and will be removed in a future version.  Use is_categorical_dtype instead
  elif pd.api.types.is_categorical(cols):
C:\Users\ferna\Anaconda3\lib\site-packages\category_encoders\utils.py:21: FutureWarning: is_categorical is deprecated and will be removed in a future version.  Use is_categorical_dtype instead
  elif pd.api.types.is_categorical(cols):
C:\Users\ferna\Anaconda3\lib\site-packages\category_encoders

In [68]:
X_train["Total_Amount"] = pd.to_numeric(X_train["Total_Amount"],errors='coerce').fillna(X_train["Total_Amount"].mean())
X_train["Opportunity_Created_Year"] = pd.to_numeric(X_train["Opportunity_Created_Year"],errors='coerce').fillna(0)
X_train["Quote_Expiry_DOY"] = pd.to_numeric(X_train["Quote_Expiry_DOY"],errors='coerce').fillna(0)
X_train["Quote_Expiry_Year"] = pd.to_numeric(X_train["Quote_Expiry_Year"],errors='coerce').fillna(0)
X_train["Planned_Delivery_End_DOY"] = pd.to_numeric(X_train["Planned_Delivery_End_DOY"],errors='coerce').fillna(0)
X_train["Planned_Delivery_End_Year"] = pd.to_numeric(X_train["Planned_Delivery_End_Year"],errors='coerce').fillna(0)

X_train = X_train.drop(columns = 'Target')

In [69]:
X_test["Total_Amount"] = pd.to_numeric(X_test["Total_Amount"],errors='coerce').fillna(test["Total_Amount"].mean())
X_test["Opportunity_Created_Year"] = pd.to_numeric(X_test["Opportunity_Created_Year"],errors='coerce').fillna(0)
X_test["Quote_Expiry_DOY"] = pd.to_numeric(X_test["Quote_Expiry_DOY"],errors='coerce').fillna(0)
X_test["Quote_Expiry_Year"] = pd.to_numeric(X_test["Quote_Expiry_Year"],errors='coerce').fillna(0)
X_test["Planned_Delivery_End_DOY"] = pd.to_numeric(X_test["Planned_Delivery_End_DOY"],errors='coerce').fillna(0)
X_test["Planned_Delivery_End_Year"] = pd.to_numeric(X_test["Planned_Delivery_End_Year"],errors='coerce').fillna(0)


## Model: Catboost

In [70]:
def cross_val(model, x_train, y_train):
    score_cross_val = model_selection.cross_val_score(model, x_train, y_train, cv=5)
    print(score_cross_val.mean())

In [71]:
def catboost(x_train, y_train, x_validation, y_validation):
    catb_classifier = CatBoostClassifier()
    params_catb = {'n_estimators': [50, 100, 150], 'learning_rate': [0.01, 0.05, 0.1], 'l2_leaf_reg': [0, 1, 5]}    
    catb_gs = GridSearchCV(catb_classifier, params_catb, cv=5)
    catb_gs.fit(x_train, y_train)
    catb_best = catb_gs.best_estimator_
    print(catb_gs.best_params_)
    print('catb: {}'.format(catb_best.score(x_validation, y_validation)))
    return catb_best

In [72]:
def catboost_2(x_train, y_train, x_validation, y_validation):
    params_catb_2={
        'n_estimators':stats.randint(10,150),'learning_rate':stats.uniform(0.01,0.3),
        'subsample':stats.uniform(0.3,0.7),'l2_leaf_reg':[1,5,10],
        'max_depth':[3,10,6],'colsample_bylevel':stats.uniform(0.,0.6)
    }
    
    catb_rs = RandomizedSearchCV(CatBoostClassifier(),
                          param_distributions=params_catb_2,
                          cv=3,
                          scoring='neg_log_loss',
                          verbose=1,
                          n_iter=150)
    
    catb_rs.fit(x_train, y_train)
    catb_best = catb_rs.best_estimator_
    print(catb_rs.best_params_)
    print('catb: {}'.format(catb_best.score(x_validation, y_validation)))
    return catb_best

In [73]:
def test_model(model, x_test, y_test):
    predictions = model.predict_proba(x_test)[:,1]
    logloss = log_loss(y_test, predictions)
    accuracy = accuracy_score(y_test, predictions.round())
    print("Accuracy: %.2f%%, Logloss: %.2f" % (accuracy*100.0, logloss))

In [89]:
def best_features(model,train):
    importance = model.feature_importances_
    result = pd.DataFrame([train.columns,importance]).transpose()
    result.columns = ["Feature","Importance"]
    return result.sort_values(by='Importance', ascending=False).head(15)["Feature"].to_list()
    
    
def plot_features(model,train):
    fig = plt.gcf()
    fig.set_size_inches(350, 350)
    selection = SelectFromModel(model, threshold=0.040, prefit=True)
    selected_dataset = selection.transform(train)
    model.plot_importance(booster=model)

    plt.rcParams["figure.figsize"] = (40,20)
    plt.xlabel("\nFeature importance", fontsize=40)
    plt.ylabel("Features", fontsize=35)
    plt.xticks(fontsize=20)
    plt.yticks(fontsize=20)
    plt.show()

### cat boost 1 with all features

In [75]:
y = train.Target
x_train, x_validation, y_train, y_validation = train_test_split(X_train, y, test_size=0.3, stratify=y)

In [76]:
catboost_model = catboost(x_train, y_train, x_validation, y_validation)
test_model(catboost_model,x_validation,y_validation)
cross_val(catboost_model, x_train, y_train)

0:	learn: 0.6844188	total: 13.3ms	remaining: 654ms
1:	learn: 0.6753059	total: 24.6ms	remaining: 589ms
2:	learn: 0.6684262	total: 36.5ms	remaining: 571ms
3:	learn: 0.6604531	total: 47.6ms	remaining: 548ms
4:	learn: 0.6542167	total: 58.9ms	remaining: 530ms
5:	learn: 0.6457623	total: 73ms	remaining: 535ms
6:	learn: 0.6379507	total: 84.3ms	remaining: 518ms
7:	learn: 0.6331695	total: 95.7ms	remaining: 503ms
8:	learn: 0.6282585	total: 108ms	remaining: 491ms
9:	learn: 0.6217104	total: 119ms	remaining: 476ms
10:	learn: 0.6153512	total: 130ms	remaining: 461ms
11:	learn: 0.6071774	total: 142ms	remaining: 450ms
12:	learn: 0.6025271	total: 154ms	remaining: 437ms
13:	learn: 0.5975421	total: 165ms	remaining: 425ms
14:	learn: 0.5915616	total: 176ms	remaining: 411ms
15:	learn: 0.5862985	total: 188ms	remaining: 400ms
16:	learn: 0.5814785	total: 200ms	remaining: 388ms
17:	learn: 0.5762211	total: 211ms	remaining: 376ms
18:	learn: 0.5711602	total: 223ms	remaining: 364ms
19:	learn: 0.5675459	total: 235ms	r

In [87]:
best_features = best_features(catboost_model,X_train)
if "Opportunity_ID" not in best_features: 
    best_features.append("Opportunity_ID")

In [78]:
y_pred = catboost_model.predict_proba(X_test)[:,1]
submission_cb = pd.DataFrame(data={'Opportunity_ID':X_test['Opportunity_ID'], 'Target': y_pred})
submission_cb = submission_cb.groupby("Opportunity_ID").agg({"Target":"mean"}).reset_index()
submission_cb.to_csv('../submits/cat_boost_with_base_n_encoding.csv', index=False)

### cat boost 1 with best features

In [79]:
X_train_best_features = X_train.loc[:,best_features]
X_test_best_features = X_test.loc[:,best_features]

In [80]:
x_best_train, x_best_validation, y_best_train, y_best_validation = train_test_split(X_train_best_features, y, test_size=0.3, stratify=y)

In [81]:
catboost_model_2 = catboost(x_best_train, y_best_train, x_best_validation, y_best_validation)
test_model(catboost_model_2,x_best_validation,y_best_validation)
cross_val(catboost_model_2, x_best_train, y_best_train)

0:	learn: 0.6886373	total: 12.7ms	remaining: 620ms
1:	learn: 0.6846651	total: 19.2ms	remaining: 461ms
2:	learn: 0.6807885	total: 25.4ms	remaining: 399ms
3:	learn: 0.6765173	total: 33.4ms	remaining: 385ms
4:	learn: 0.6723353	total: 39.9ms	remaining: 359ms
5:	learn: 0.6681899	total: 46.5ms	remaining: 341ms
6:	learn: 0.6641072	total: 53ms	remaining: 326ms
7:	learn: 0.6601301	total: 59.6ms	remaining: 313ms
8:	learn: 0.6565229	total: 66.4ms	remaining: 303ms
9:	learn: 0.6528736	total: 73.7ms	remaining: 295ms
10:	learn: 0.6492366	total: 80ms	remaining: 284ms
11:	learn: 0.6456983	total: 86.5ms	remaining: 274ms
12:	learn: 0.6422413	total: 93.7ms	remaining: 267ms
13:	learn: 0.6390688	total: 99.7ms	remaining: 256ms
14:	learn: 0.6355650	total: 106ms	remaining: 247ms
15:	learn: 0.6320473	total: 113ms	remaining: 240ms
16:	learn: 0.6287456	total: 120ms	remaining: 233ms
17:	learn: 0.6254129	total: 126ms	remaining: 224ms
18:	learn: 0.6222559	total: 133ms	remaining: 217ms
19:	learn: 0.6190633	total: 139

In [82]:
y_pred_2 = catboost_model_2.predict_proba(X_test_best_features)[:,1]
submission_cb_2 = pd.DataFrame(data={'Opportunity_ID':X_test_best_features['Opportunity_ID'], 'Target': y_pred_2})
submission_cb_2 = submission_cb_2.groupby("Opportunity_ID").agg({"Target":"mean"}).reset_index()
submission_cb_2.to_csv('../submits/cat_boost_best_features_with_base_n_encoding.csv', index=False)

### cat boost 2 with all features

In [83]:
catboost_model_3 = catboost_2(x_train, y_train, x_validation, y_validation)
test_model(catboost_model_3,x_validation,y_validation)
cross_val(catboost_model_3, x_train, y_train)

Fitting 3 folds for each of 150 candidates, totalling 450 fits
0:	learn: 0.6374882	total: 7.5ms	remaining: 135ms
1:	learn: 0.5967954	total: 14.1ms	remaining: 120ms
2:	learn: 0.5574300	total: 21.2ms	remaining: 113ms
3:	learn: 0.5325104	total: 27.9ms	remaining: 105ms
4:	learn: 0.5113501	total: 35.3ms	remaining: 98.8ms
5:	learn: 0.4922754	total: 42.2ms	remaining: 91.4ms
6:	learn: 0.4783797	total: 48.7ms	remaining: 83.4ms
7:	learn: 0.4703816	total: 57ms	remaining: 78.4ms
8:	learn: 0.4577168	total: 67.4ms	remaining: 74.9ms
9:	learn: 0.4521875	total: 73ms	remaining: 65.7ms
10:	learn: 0.4440620	total: 79.8ms	remaining: 58.1ms
11:	learn: 0.4367252	total: 89.7ms	remaining: 52.3ms
12:	learn: 0.4266805	total: 120ms	remaining: 55.5ms
13:	learn: 0.4224193	total: 127ms	remaining: 45.3ms
14:	learn: 0.4179003	total: 133ms	remaining: 35.5ms
15:	learn: 0.4130972	total: 158ms	remaining: 29.5ms
16:	learn: 0.4085748	total: 165ms	remaining: 19.4ms
17:	learn: 0.4033080	total: 171ms	remaining: 9.49ms
18:	lear

In [91]:
best_features_2 = best_features(catboost_model_3,X_train)
if "Opportunity_ID" not in best_features_2: 
    best_features_2.append("Opportunity_ID")

In [92]:
y_pred_3 = catboost_model_3.predict_proba(X_test)[:,1]
submission_cb_3 = pd.DataFrame(data={'Opportunity_ID':X_test['Opportunity_ID'], 'Target': y_pred_3})
submission_cb_3 = submission_cb_3.groupby("Opportunity_ID").agg({"Target":"mean"}).reset_index()
submission_cb_3.to_csv('../submits/cat_boost_2_with_base_n_encoding.csv', index=False)

### cat boost 2 with best features

In [93]:
X_train_best_features_2 = X_train.loc[:,best_features_2]
X_test_best_features_2 = X_test.loc[:,best_features_2]

In [94]:
x_best_train_2, x_best_validation_2, y_best_train_2, y_best_validation_2 = train_test_split(X_train_best_features_2, y, test_size=0.3, stratify=y)

In [95]:
catboost_model_4 = catboost_2(x_best_train_2, y_best_train_2, x_best_validation_2, y_best_validation_2)
test_model(catboost_model_4,x_best_validation_2,y_best_validation_2)
cross_val(catboost_model_4, x_best_train_2, y_best_train_2)

Fitting 3 folds for each of 150 candidates, totalling 450 fits
0:	learn: 0.6684645	total: 2.63ms	remaining: 34.2ms
1:	learn: 0.6413618	total: 5.65ms	remaining: 33.9ms
2:	learn: 0.6077304	total: 8.93ms	remaining: 32.7ms
3:	learn: 0.5649217	total: 12.2ms	remaining: 30.4ms
4:	learn: 0.5470335	total: 17.2ms	remaining: 30.9ms
5:	learn: 0.5236089	total: 20.2ms	remaining: 26.9ms
6:	learn: 0.5145337	total: 23.1ms	remaining: 23.1ms
7:	learn: 0.4942392	total: 25.9ms	remaining: 19.4ms
8:	learn: 0.4790274	total: 28.6ms	remaining: 15.9ms
9:	learn: 0.4790041	total: 30.5ms	remaining: 12.2ms
10:	learn: 0.4683758	total: 34ms	remaining: 9.27ms
11:	learn: 0.4575332	total: 37ms	remaining: 6.17ms
12:	learn: 0.4498783	total: 39.7ms	remaining: 3.06ms
13:	learn: 0.4426046	total: 42.8ms	remaining: 0us
0:	learn: 0.6619438	total: 2.52ms	remaining: 32.8ms
1:	learn: 0.6336730	total: 5.53ms	remaining: 33.2ms
2:	learn: 0.5974659	total: 8.38ms	remaining: 30.7ms
3:	learn: 0.5584439	total: 11.3ms	remaining: 28.1ms
4:	l

In [96]:
y_pred_4 = catboost_model_4.predict_proba(X_test_best_features_2)[:,1]
submission_cb_4 = pd.DataFrame(data={'Opportunity_ID':X_test_best_features_2['Opportunity_ID'], 'Target': y_pred_4})
submission_cb_4 = submission_cb_4.groupby("Opportunity_ID").agg({"Target":"mean"}).reset_index()
submission_cb_4.to_csv('../submits/cat_boost_2_best_features_with_base_n_encoding.csv', index=False)